First, we need to import a few packages that you should have installed during the past few days already. If you encounter any issues with this, please let one of the presenters know. 

The notebook should work with the following versions: 
- qiskit=0.43.1
- qiskit-aer=0.12.0
- qutip=4.7.1
- numpy=1.23.5
- scipy=1.10.1
- cma=3.3.0

In [ ]:
import numpy as np
from qutip import qeye, sigmax, sigmay, sigmaz, tensor, Qobj
import sys
import math

# Motivation and Introduction

Let us first define the Heisenberg Kagome spin model for different number of sites $N$. The Kagome lattice is a two-dimensional lattice that consists of corner shared triangles. The spins $\sigma_i = (X_i, Y_i, Z_i)$ are located at the vertices of the lattice $i = 1, ..., N$. Each spin interacts antiferromagnetically with all of its nearest neighbor spins along the bonds of the lattice. Since each spin is a member of two triangular units, we can write the full Hamiltonian (=energy functional) of the Kagome Heisenberg model as $H = \sum_{\text{triangles} t} (S_{t,1} + S_{t,2} + S_{t,3})^2$. 

To gain some intuition, let us first think of a model of classical spins, which are three-dimensional unit vectors. This functional is minimized whenever all the terms in brackets vanish, i.e., the total spin on each triangle vanishes. There are many ways for the three spins on a triangle to sum up to zero. Therefore, the ground state is thus extensively degenerate, i.e., there is a continuous degree of freedom on every plaquette that can vary without changing the ground state energy. 

The main question is whether quantum fluctuations lift this extensive ground state degeneracy and what is the quantum ground state and its energy. This is a very difficult problem that has inspired researchers in condensed matter physics since many years (see https://www.nature.com/articles/nature08917). It is also relevant from an experimental point of view as there are magnetic materials with $S=1/2$ moments where the magnetic ions are arranged on a kagome lattice (for example the material Herbertsmithite, see https://doi.org/10.1103/RevModPhys.88.041002). It has also been the topic of the IBM Quantum Awards: Open Science Prize 2022: https://github.com/qiskit-community/open-science-prize-2022 and https://research.ibm.com/blog/ibm-quantum-open-science-prize-2022.

We can represent the Hamiltonian as a sum of Pauli strings. The N=5 Kagome Ising model (just ZZ interactions) can then be written as $H = ZZIII + IZZII + ZIZII + IIZZI + IIZIZ + IIIZZ$. We encode this using a list of strings as follows:  ["1.0\*ZZIII", "1.0\*IZZII", ...]. The N=5 Kagome Heisenberg model contains also $XX$ and $YY$ terms, i.e., $H = XXIII + YYIII + ZZIII + ...$ (total of 18 terms).
By mapping the strings "X", "Y", "Z" to the three Pauli matrices and forming tensor products, we can build the Hamiltoniam matrix. This matrix has dimension dim = $2^N$. For $N=5$ it is thus 32 dimensional. 
The function `map_hamiltonian()` maps the list of Pauli strings with numerical prefactors ["1.0\*ZZIII", "1.0\*IZZII", ...] to a Hamiltonian matrix that is the tensor product of Pauli matrices.

In [ ]:
def map_hamiltonian(s_list):
    '''
    Write down the original string of spin-S operators in terms of Pauli
    matrices, while respecting the chosen encoding
    '''
    pauli = [qeye(2), sigmax(), sigmay(), sigmaz()]

    pm_dict = {"I": pauli[0], "X": pauli[1], \
                        "Y": pauli[2], "Z": pauli[3]}

    op_total = 0.
    for op in s_list:
        coef, label = float(op.split('*')[0]), op.split('*')[1]
        op_total += float(coef)*tensor([pm_dict[x] for x in label])

    return op_total


## Warmup: Few site models

Let's play with this function first to see that we understand it well. Consider models of just two spins, first with just $ZZ$ interations (also called Ising model) and then one with symmetric $XX, YY, ZZ$ interactions (the Heisenberg model). 

Let's first look at the Hamiltonian of the two-site antiferromagnetic (AFM) Ising model with Hamiltonian $H = ZZ$. Its ground states are |01> and |10> with energy $E_GS = -1.0$.

In [ ]:
map_hamiltonian(["1.0*ZZ"])

Now consider the Hamiltonian of the two-site antiferromagnetic (AFM) Heisenberg model with Hamiltonian $H = XX + YY + ZZ$.

In [ ]:
map_hamiltonian(["1.0*XX", "1.0*YY", "1.0*ZZ"])

The ground and lowest excited states are of particular interest as they often show unique physical behavior and are accessible by cooling an experimental system that realizes the Hamiltonian (examples exist in cold atoms, but also real materials). 
We define a function `get_lowest_states()` that returns a tuple containing the lowest `num` eigenvalues and eigenstates. The first element of the tuple contains the num lowest energies. The second entry contains the num lowest states following qutip output format for kets. The Qobj data part contains the ground state vector in the basis used to define the Hamiltonian (here (|00>, |01>, |10>, |11>)). 

In [ ]:
def get_lowest_states(hamiltonian, num):
    '''
    get the lowest num eigenvalues and eigenstates.
    '''
    dim = hamiltonian.shape[0]
    w, v = hamiltonian.eigenstates(eigvals=num, sparse=dim>4)
    return w, v

Using the function `get_lowest_states()`, we find that the ground state energy of the two-site Heisenberg AFM model. We find $E_{GS} = -3$ and the ground state is $|GS> = (|10> - |01>)/\sqrt{2}$. This state is called a singlet and has total spin $S=0$. 


In [ ]:
ham = map_hamiltonian(["1.0*XX", "1.0*YY", "1.0*ZZ"])
get_lowest_states(ham, 2)

Now we define a Heisenberg model for three sites on a triangle and answer the following questions
1. What is the ground state energy $E_{GS}$?
2. Is the GS unique or are there multiple ground states (how many)?

In [ ]:
ham = map_hamiltonian(["1.0*XXI", "1.0*YYI", "1.0*ZZI","1.0*XIX", "1.0*YIY", "1.0*ZIZ","1.0*IXX", "1.0*IYY", "1.0*IZZ"])
lowest_states=get_lowest_states(ham, 5)
lowest_energies=lowest_states[0]
lowest_energies

The ground state energy is $E_{GS} = -3$ and there are four degenerate ground states. Three spin 1/2 add up to $\frac12 \otimes \frac12 \otimes \frac12 = (0 \oplus 1) \otimes \frac12 = \frac12 \oplus \frac12 \oplus \frac32$. The spin 1/2 states are all degenerate. 

In [ ]:
# ToDo: Answer the following questions:
# What happens if you make the coupling between XX and YY components slightly smaller than the coupling between the ZZ components? 
# What are the eigenenergies and their degeneracies for this anisotropic model ? How do the eigenstates look like?
# Add a three-spin interaction term to the system. Does this break the degeneracy?

## 5-site Kagome Heisenberg model: exact solution

Let's first define the five-site Kagome Heisenberg Hamiltonian. We can do it by hand or use some basic Python functions for manipulating strings. 
We define a list of bonds `bonds_kagome_5` across which the Heisenberg interaction acts. This can be easily generalized to larger systems. 

In [ ]:
ham_kagome_5 = []
kagome_5_paulis = []
s = 'III'
bonds_kagome_5 = [[0,1], [0,2], [1,2], [2,3], [2,4], [3,4]]
for pauli in ["X", "Y", "Z"]:
    for bond in bonds_kagome_5: 
        list_s = list(s)
        list_s.insert(bond[0], pauli)
        list_s.insert(bond[1], pauli)
        if pauli == "X":
            pauli_string="1.0*" + ''.join(list_s)
        elif pauli == "Y":
            pauli_string="1.0*" + ''.join(list_s)
        elif pauli == "Z":
            pauli_string="1.0*" + ''.join(list_s)
        kagome_5_paulis.append(''.join(list_s))
        ham_kagome_5.append(pauli_string)

In [ ]:
#ToDo: Look at the list of Pauli strings. 
# Make sure that you understand which bond interaction on the 5-site Kagome lattice each term in the list represents. 
# For this you can execute: ham_kagome_5 in a separate cell

Let's now compute the lowest few state of the five-site Kagome Heisenberg model. 

In [ ]:
ham= map_hamiltonian(ham_kagome_5)
lowest_states=get_lowest_states(ham, 20)
lowest_energies=lowest_states[0]
lowest_energies

The ground state energy is $E_{GS} = -6$ and it is sixfold degenerate. We see that the $N=5$ system has an large ground state degeneracy that is proportional to the number of spins. In fact, the classical Kagome Heisenberg model exhibits an extensive ground state degeneracy, i.e., the number of degenerate ground states scales with the number of spins in the system. This large degeneracy will be lifted by quantum fluctuations, e.g. by forming a superposition of classically degenerate configurations. This large classical degeneracy lies at the root of the intriguing behavior of the Kagome Heisenberg model. 

Let's compare this to the Heisenberg model on a 5-site chain.

ToDo: draw the lattice that contains five sites (as vertices) and the bonds between sites that appear in the list "bonds_chain_5" in the cell below. 

In [ ]:
ham_chain_5 = []
chain_5_paulis = []
s = 'III'
bonds_chain_5 = [[0,1], [1,2], [2,3], [3,4]]
for pauli in ["X", "Y", "Z"]:
    for bond in bonds_chain_5: 
        list_s = list(s)
        list_s.insert(bond[0], pauli)
        list_s.insert(bond[1], pauli)
        if pauli == "X":
            pauli_string="1.0*" + ''.join(list_s)
        elif pauli == "Y":
            pauli_string="1.0*" + ''.join(list_s)
        elif pauli == "Z":
            pauli_string="1.0*" + ''.join(list_s)
        chain_5_paulis.append(''.join(list_s))
        ham_chain_5.append(pauli_string)

The ground state of the 5-site Heisenberg chain is doubly degenerate (due to site inversion symmetry at the center site). The GS energy is $E_{GS} = -7.71$.

In [ ]:
ham = map_hamiltonian(ham_chain_5)
lowest_states=get_lowest_states(ham, 20)
lowest_energies=lowest_states[0]
lowest_energies

In [ ]:
#ToDo: Create a list of bonds that corresponds to a chain with eight sites. Is the ground state degenerate or unique?

## 9-site Kagome Heisenberg model

We add the additional bonds that exist for the $N=9$ site system to the list of bonds. The Hilbert space of the nine-site system is $2^9=512$.

In [ ]:
ham_kagome_9 = []
s = 'IIIIIII'
bonds_kagome_9 = [[0,1], [0,2], [1,2], [2,3], [2,4], [3,4], [4,5], [4,6], [5,6], [6,7], [6,8], [7,8]]
for pauli in ["X", "Y", "Z"]:
    for bond in bonds_kagome_9: 
        list_s = list(s)
        list_s.insert(bond[0], pauli)
        list_s.insert(bond[1], pauli)
        pauli_string="1.0*" + ''.join(list_s)
        ham_kagome_9.append(pauli_string)

#ham_kagome_9

In [ ]:
# Look at the list of Pauli strings that define the 9-site Kagome model. 
# Identify each term with a certain bond interaction term on the lattice.

The ground state energy is $E_{GS} = -12$ and the ground state is tenfold degenerate. Note that the two hourglass motifs are only connected at a single site, so we need to go to the 12 site system to see the full 2D nature of the Kagome system, where three hourglasses close to form the Star of David motif.  

In [ ]:
ham = map_hamiltonian(ham_kagome_9)
lowest_states=get_lowest_states(ham, 20)
lowest_energies=lowest_states[0]
lowest_energies

## 12-site Kagome Heisenberg model

The Hilbert space of the 12-site system has dimension $2^{12} = 4096$. 

In [ ]:
ham_kagome_12 = []
s = 'IIIIIIIIII'
bonds_kagome_12 = [[0,1], [0,2], [1,2], [2,3], [2,4], [3,4], [4,5], [4,6], [5,6], [6,7], [6,8], [7,8], [8,9], [8,10], [9,10], [10,11], [10,1], [11,1]]
for pauli in ["X", "Y", "Z"]:
    for bond in bonds_kagome_12: 
        list_s = list(s)
        list_s.insert(bond[0], pauli)
        list_s.insert(bond[1], pauli)
        pauli_string="1.0*" + ''.join(list_s)
        ham_kagome_12.append(pauli_string)

#ham_kagome_12

The 12-site Kagome Heisenberg Hamiltonian has a unique ground state with ground state energy $E_{GS} = 21.312$, i.e., quantum flucutations indeed lift the extensive degeneracy of the classical model. The first excited states are nearby in energy. 

We now want to reproduce the GS energy with the help of quantum computers. The reason is that this will potentially allow us to scale up the approach to larger systems, which cannot be treated on classical hardware due to the exponential growth of the Hilbert space with the number of spins. 

In [ ]:
ham = map_hamiltonian(ham_kagome_12)
lowest_states=get_lowest_states(ham, 10)
lowest_energies=lowest_states[0]
lowest_energies

In [ ]:
# Optional ToDo: 
# 1. Add more sites to your Kagome cluster and see how for many sites you can solve for the ground state energy in reasonable time (say 30 sec) 
# using the method above. 

# Variational Quantum Eigensolver for 5-site model

## Loading qiskit packages and introduce backend

Import a few packages needed from Qiskit

In [ ]:
from qiskit import QuantumCircuit, Aer, transpile, ClassicalRegister
from qiskit.visualization import plot_gate_map, plot_error_map
from qiskit.providers.fake_provider import FakeGuadalupeV2

Here we use the fake backend corresponding to ibmq_guadalupe, which was used in the 2023 IBM Quantum Challenge. 

In [ ]:
backend = FakeGuadalupeV2()

In [ ]:
plot_gate_map(backend)

In [ ]:
plot_error_map(backend)

When mapping your model onto the physical qubits of the quantum chip, you need to be aware that the single and two-qubit error rates depend on the qubits involved. How you map your model onto the physical qubits of the device therefore largely affect the quality of the result. Also, the layout of the physical qubits is a heavy-hexagon lattice and not a Kagome lattice. That means that some nearest-neighbor spins on the Kagome are not nearest-neighbors on the device and the circuit thus needs to include additional SWAP operations (=3 CNOT gates). This increases the circuit depth and minimizing the number of required SWAPs is therefore very important. 
ToDo: this about a good mapping of the spins of the model to the physical qubits [0,1,2,3,4] -> [...]. This can be controlled below using the parameter `initial_layout`.

## Hamiltonian Variational Ansatz (HVA)

Define circuit and measure energy for given variational state. VQE is a heuristic approach whose performance depends on the choice of the form of the variational wavefunction also called the parametrized quantum circuit (PQC). Here, we use a common PQC called the Hamiltonian Variational Ansatz (HVA) that is inspired by Trotterized time evolution under a given Hamiltonian H. It contains $N_\ell$ layers that repeat, each layer is of the form $U_l =   e^{-i \theta_{ZZ}^{(l)} \sum_{\langle i,j \rangle} Z_i Z_j}   e^{-i \theta_Z^{(l)} \sum_i Z_i} e^{-i \theta_{YY}^{(l)} \sum_{\langle i,j \rangle} Y_i Y_j} e^{-i \theta_Y^{(l)} \sum_i Y_i} e^{-i \theta_{XX}^{(l)} \sum_{\langle i,j \rangle} X_i X_j} e^{-i \theta_X^{(l)}\sum_i X_i} $. 

The following cell defines a circuit of a single layer of the HVA ansatz, taking six parameters $\theta_\alpha$. You can change the number of qubits and the bonds_all variable specifies which XX, YY, ZZ terms are included in the summations. 

In [ ]:
# vqe layer for Guadalupe geometry using a certain qubit mapping
def vqeLayer(params, num_qubits = 5, bonds_all = [[0,1], [0,2], [1,2], [2,3], [2,4], [3,4]]):
    if (len(params) != 6):
        print("Length or parameter list should be six. ")
    
    theta_XX = params[0]
    theta_YY = params[1]
    theta_ZZ = params[2]
    theta_X = params[3]
    theta_Y = params[4]
    theta_Z = params[5]
    
    vqeLayer = QuantumCircuit(num_qubits)
    
    vqeLayer.rx(2.*theta_X, range(num_qubits))

    for bonds in bonds_all:
        vqeLayer.h(bonds[0])
        vqeLayer.h(bonds[1])
        vqeLayer.cx(bonds[0], bonds[1])
        vqeLayer.rz(2.*theta_XX, bonds[1])
        vqeLayer.cx(bonds[0], bonds[1])
        vqeLayer.h(bonds[0])
        vqeLayer.h(bonds[1])   

    vqeLayer.barrier()

    vqeLayer.ry(2.*theta_Y, range(num_qubits))

    for bonds in bonds_all:
        vqeLayer.rx(np.pi/2, bonds[0])
        vqeLayer.rx(np.pi/2, bonds[1])
        vqeLayer.cx(bonds[0], bonds[1])
        vqeLayer.rz(2.*theta_YY, bonds[1])
        vqeLayer.cx(bonds[0], bonds[1])
        vqeLayer.rx(-np.pi/2, bonds[0])
        vqeLayer.rx(-np.pi/2, bonds[1])

    vqeLayer.barrier()

    vqeLayer.rz(2.*theta_Z, range(num_qubits))
    
    for bonds in bonds_all:
        vqeLayer.cx(bonds[0], bonds[1])
        vqeLayer.rz(2.*theta_ZZ, bonds[1])
        vqeLayer.cx(bonds[0], bonds[1])

    return vqeLayer

To measure the expectation value of the Heisenberg Hamiltonian $H = \sum_{\langle i, j \rangle} (X_i X_j + Y_i Y_j + Z_i Z_j)$ in the variational state $E(\{\theta_i\}) = \langle \psi(\{\theta_i\})|H | \psi(\{\theta_i\})\rangle$, we need to prepare three different kinds of circuits: one with a final measurement of all the qubits in the X basis, one with a final measurement in the Y basis and one in the Z basis.

In [ ]:
def makevqeCircuit_meas_X(params, num_layers = 1, bonds_all = bonds_kagome_5, num_qubits = 5):
    if (len(params)%6 != 0):
        print("Length or parameter list should be multiple of six. ")
    vqeCircuit = QuantumCircuit(num_qubits)
    vqeCircuit.barrier()
    for i in range(num_layers):
        vqeL = vqeLayer(params[6*i:6*(i+1)], num_qubits = num_qubits, bonds_all = bonds_all)
        vqeCircuit = vqeCircuit.compose(vqeL)
        vqeCircuit.barrier()

    vqeCircuit.h(range(num_qubits)) # measure in the X basis

    return vqeCircuit 

In [ ]:
def makevqeCircuit_meas_Y(params, num_layers = 1, bonds_all = bonds_kagome_5, num_qubits = 5):
    if (len(params)%6 != 0):
        print("Length or parameter list should be multiple of six. ")
    vqeCircuit = QuantumCircuit(num_qubits)
    vqeCircuit.barrier()
    for i in range(num_layers):
        vqeL = vqeLayer(params[6*i:6*(i+1)], num_qubits = num_qubits, bonds_all = bonds_all)
        vqeCircuit = vqeCircuit.compose(vqeL)
        vqeCircuit.barrier()

    vqeCircuit.sdg(range(num_qubits)) # measure in the Y basis
    vqeCircuit.h(range(num_qubits)) # measure in the Y basis
    
    return vqeCircuit

In [ ]:
def makevqeCircuit_meas_Z(params, num_layers = 1, bonds_all = bonds_kagome_5, num_qubits = 5):
    if (len(params)%6 != 0):
        print("Length or parameter list should be multiple of six. ")
    vqeCircuit = QuantumCircuit(num_qubits)
    vqeCircuit.barrier()
    for i in range(num_layers):
        vqeL = vqeLayer(params[6*i:6*(i+1)], num_qubits = num_qubits, bonds_all = bonds_all)
        vqeCircuit = vqeCircuit.compose(vqeL)
        vqeCircuit.barrier()

    return vqeCircuit 

In [ ]:
#ToDo: 
# draw the different circuits and recognize the different parts of the Hamiltonian Variational Ansatz in the circuit. 
# you can use the commands: 
# qc = makevqeCircuit_meas_Z(params)
# qc.draw()

### Statevector VQE optimization

Now, let's run VQE to determine the optimal parameters for the HVA quantum circuit with $N_\ell$ layers. We first do this using an exact statevector simulation that has access to the full wavefunction of the system. We also need to fix an initial reference state (which we choose to be the state |000...> here) and the initial value of the VQE parameters (which we choose to be random within some interval around zero).

We use big endian notation when defining the Hamiltonian matrix above (i.e. the lowest bit is on the left of the string, e.g. "XXIII" has X on site 0 and 1), but Qiskit uses little endian notation, i.e., the lowest bit is on the right. The following function transforms a vector from little endian (output of qiskit statevector calculation) to big endian notation (to compute the Hamiltonian expectation value as $\langle \psi | H |\psi\rangle)$.

In [ ]:
def little_to_big_endian(wavefunction, n_qubit):
    s, nq = wavefunction, n_qubit
    sp = s.reshape([2 for j in range(nq)])
    swap_no = math.floor(nq / 2)
    for j in range(swap_no):
        sp = np.swapaxes(sp, j, nq - 1 - j)
    sp = sp.reshape(2**nq)
    return(sp)

We define the expectation value of the Hamiltonian in the state generated by the parametrized quantum circuit acting on a fixed initial reference state (here |0000...>). Note that the reference state is hard-coded into the circuit function `makevqeCircuit_meas_Z` here.

To make sure that the variable `bonds_kagome_5` is defined, we copy this cell from the first section of the notebook.

In [ ]:
ham_kagome_5 = []
kagome_5_paulis = []
s = 'III'
bonds_kagome_5 = [[0,1], [0,2], [1,2], [2,3], [2,4], [3,4]]
for pauli in ["X", "Y", "Z"]:
    for bond in bonds_kagome_5: 
        list_s = list(s)
        list_s.insert(bond[0], pauli)
        list_s.insert(bond[1], pauli)
        if pauli == "X":
            pauli_string="1.0*" + ''.join(list_s)
        elif pauli == "Y":
            pauli_string="1.0*" + ''.join(list_s)
        elif pauli == "Z":
            pauli_string="1.0*" + ''.join(list_s)
        kagome_5_paulis.append(''.join(list_s))
        ham_kagome_5.append(pauli_string)

In [ ]:
def ham_pqc_sv(params, num_layers = 1, bonds_all = bonds_kagome_5, num_qubits = 5):
    vqe_circuit=makevqeCircuit_meas_Z(params, num_layers = num_layers, bonds_all = bonds_all, num_qubits = num_qubits)
    state = np.array(Aer.get_backend('statevector_simulator').run(vqe_circuit).result().get_statevector())
    state_tf = little_to_big_endian(state, num_qubits)
    if bonds_all == bonds_kagome_5:     
        ham_matrix = np.array(map_hamiltonian(ham_kagome_5))
    else:
        print("Hamiltonian matrix not defined.")
    res = np.vdot(state_tf, ham_matrix.dot(state_tf))
    return res

In [ ]:
#ToDo: 
# What is the energy of the state |00000>?
# What is the energy of the state |01010>?

We use a classical optimizer that is built into scipy, so we need to import that package. 

In [ ]:
import scipy

We define the cost function as the expectation value of the Hamiltonian in the variational state. We use the BFGS method for optimization, which uses the gradient of the cost function as well (which is computed numerically here).

In [ ]:
def fun_cost(params, num_layers, bonds_all, num_qubits):
    ham = np.real(ham_pqc_sv(params, num_layers = num_layers, bonds_all = bonds_all, num_qubits = num_qubits))
    return ham

def vqe_optimization_sv(init_params, num_layers = 1, bonds_all = bonds_kagome_5, num_qubits = 5):
    res = scipy.optimize.minimize(fun_cost, init_params, args=(num_layers, bonds_all, num_qubits), method='BFGS')
    return res.fun, res

Running the optimization for a given set of initial parameters. We find that the optimal GS value for a single HVA layer is $E_{VQE,l=1} = -3.79$, which is quite far away from the exact GS energy $E_{GS} = -6$. This is due to a limitation of the ansatz and one could study deeper circuits (e.g. more layers) or different PQCs. Note that deeper circuits also contain more parameters, which makes the optimization step more difficult. 


In [ ]:
init_params = np.random.uniform(-np.pi/7, np.pi/7, 6)
res_vqe_sv=vqe_optimization_sv(init_params)
res_vqe_sv

In [ ]:
params_optimal = [-1.070e+01, 1.965e+00, -5.516e+00, 4.712e+00, 1.694e+00, 2.114e-01]

ToDo:
1. Study the dependence on the initial parameter value `init_params`. Run the optimization for 100 different random initial states, plot a histogram of the results and pick the global minimum. 
2. Study the dependence on the initial reference state on the hardware. Here, we are using the state |00000>. How do the results of item 1 look like when you initialize in other state such as |01010> or |+++++>?
3. Explore deeper circuits by systematically increasing the number of layers. Plot the dependence of the global minimum of 100 random initial states versus number of layers. Are you able to reach the exact ground state energy $E_{GS} = -6$? 
4. Explore bigger systems with $N=9$ and $N=12$ sites. 
5. Explore other optimizers that are available in scipy by changing the `method` option in the function vqe_optimization_sv.

### QASM VQE optimization

Now, let's do the VQE optimization using actual circuit executions. This makes the classical optimization much more challenging since the cost function is now noisy and fluctuates from execution to execution. First, we consider perfect gates (noiseless) and only consider the effect of shot noise due to the finite number of measurements. Importantly, as noticed above, to determine the expectation value of the Hamiltonian for a given set of variational parameter, we need to execute the parametrized quantum circuits (PQCs) three times with final measurements in the X, Y, and Z basis, respectively. 

When simulating circuit executions, we need to add measurement gates at the end of the circuit, which store the measured bitstring in a classical register (of length equal to the number of active qubits = num_qubits). Since we need to compute both XX, YY, and ZZ expectation values, we execute three types of circuits, each of then `shots` number of times. 

Another important issue is how the model is mapped onto hardware. The `initial_layout` variable defines the mapping of virtual (label of sites in the model) to physical qubits on the chip. Due to the different connectivities of the graph that is being simulated (the kagome lattice) and the ibmq_guadalupe chip (heavy-hexagon lattice), different mappings result in different circuit depths. This does not make a difference for noiseless gates, but has a large effect if one considers the effect of noisy gates. 

In [ ]:
def expectation_values(circuits, choice_backend = "noisy", shots = 8192, bonds_all = bonds_kagome_5, num_qubits = 5, initial_layout = [3, 2, 1, 0, 4]): 
    noisyresult = []
    for circ in circuits:
        # run all three types of circuits: same circuit with X, Y, Z measurements at the end, respectively 
        qc = circ.copy()
        cr = ClassicalRegister(num_qubits,'creg')
        qc.add_register(cr)
        qc.measure(range(num_qubits), range(num_qubits)) 
        qc = transpile(qc, backend, initial_layout = initial_layout)
                
        if choice_backend == "noisy":
            count=backend.run(qc, shots=shots).result().get_counts()
        elif choice_backend == "qasm":
            count=Aer.get_backend('qasm_simulator').run(qc, shots=shots).result().get_counts()
        else: 
            print("Incorrect entry of variable choice_backend.")

        count = {tuple(int(k) for k in key):count[key] for key in count.keys()}

        num = [0 for _ in range(len(bonds_all))]
        tot = [0 for _ in range(len(bonds_all))]

        for key in count.keys():
            for i, bonds in enumerate(bonds_all): 
                num[i] = (-1)**int(key[num_qubits - 1 - bonds[0]]) * (-1)**int(key[num_qubits - 1 - bonds[1]])
                tot[i] += int(num[i]*count[key])

        for i, bonds in enumerate(bonds_all): 
            noisyresult.append(1.0*tot[i]/(shots))

    return sum(noisyresult)

Let us unpack this function a bit. First we add measurement gates to the VQE circuits and transpile. Transpilation means that define a mapping of virtual qubits to physical qubits of a given hardware geometry and that we compile the circuit into the native gates that are being executed on the hardware. For example, this means that SWAP gates are included whenever CNOT gates in the VQE circuit appear between sites that are not nearest neighbors on the hardware. This means that the transpiled circuit length can differ from the original one.  

In [ ]:
circ = makevqeCircuit_meas_X(params_optimal, num_layers = 1, bonds_all = bonds_kagome_5, num_qubits = 5)
qc = circ.copy()
cr = ClassicalRegister(5,'creg')
qc.add_register(cr)
qc.measure(range(5), range(5)) 
qc = transpile(qc, backend, initial_layout = [3, 2, 1, 0, 4])

#qc.draw()


ToDo: 
1. look at the circuit and identify the different gates of the HVA layer. 
2. change the initial layout parameter and observe additional SWAP gates appearing in the circuit. 

Next, we execute the circuit on either a noiseless `qasm` simulator or a `noisy` backend. The final measurements yields a bitstring of length `num_qubits`, which is equal to five here. This is because a measurement in the X basis (same for Y and Z) yields an eigenvalue of X (here encoded as 0 -> eigenvalue +1 and 1 -> eigenvalue -1). The probability to find a certain eigenvalue of course depends on the wavefunction amplitude of that respective basis state and thus on the variational state. There are $2^5 = 32$ bitstrings (= computational basis states) in total. The parameter `shots` determines how often the circuit is being executed and thus how many bitstrings we obtain. 

The variable count contains the list of bitstrings that were obtained as well as the number of times they were found. 

In [ ]:
shots_Val = 8192
count=Aer.get_backend('qasm_simulator').run(qc, shots=shots_Val).result().get_counts()
#count

ToDo: 
1. Look at the count object. Note that this is the result for the optimal parameter values of a single layer HVA. 
2. Determine the bitstrings with the largest three count numbers. 
2. Plot a historgram of the counts, potentially plotting those above some user-defined threshold. 

Next, we use the counts to compute the expectation values $X_i X_j$ for all bonds on the kagome lattice. 

In [ ]:
num_qubits = 5

noisyresult = []
count = {tuple(int(k) for k in key):count[key] for key in count.keys()}

num = [0 for _ in range(len(bonds_kagome_5))]
tot = [0 for _ in range(len(bonds_kagome_5))]

for key in count.keys(): # loop over all bitstrings in the count dictionary
    for i, bonds in enumerate(bonds_kagome_5): # loop over all bonds (i,j) that we need to compute X_i X_j for
        num[i] = (-1)**int(key[num_qubits - 1 - bonds[0]]) * (-1)**int(key[num_qubits - 1 - bonds[1]]) # compute X_i X_j for that bitstring. Notice that the bitstring is in little endian notation, but our bonds variables are defined in big endian notation
        tot[i] += int(num[i]*count[key]) # Averaging of counts: multiply the sign of X_i X_j for that bitstring (=num[i]) with the number of of times that bitstring was found (=count[key])

for i, bonds in enumerate(bonds_kagome_5): 
    noisyresult.append(1.0*tot[i]/(shots_Val)) # populate list of bond expectatin values. Divide by the number of shots to get the average

noisyresult

ToDo: 
1. Systematically vary the number of shots `shots_Val` between $2^{12}$ and $2^{16}$ and plot the first and second expectation value in the list versus `shots_Val`. 
2. Then evaluate each circuit 10 times to obtain 10 expectation values for each value of `shots_Val`. Compute the average and standard deviation. How does the standard deviation depend on `shots_Val`? Plot the average with standard deviation versus `shots_Val`. 
3. Why do you only find two numbers for the six different expectation values?

Finally, we sum over all these expectation values to return $\sum_{\langle i,j \rangle} X_i X_j$, which is the XX part of the Kagome Heisenberg Hamiltonian. We then repeat this for the Y and Z measurement circuits and sum everything together to obtain $\langle \psi(\{\theta_i\}) | H | \psi(\{\theta_i\}) \rangle$. 

In [ ]:
sum(noisyresult)

Now we use the function `expectation_values` to define the function `ham_pqc` that returns the expectation value of the Heisenberg Hamiltonian in a given variational state using circuit executions. The variational state is defined via `params` and the parameters that define the HVA ansatz (`num_layers, bonds_all, num_qubits`). 

In [ ]:
def ham_pqc(params, num_layers = 1, choice_backend = "noisy", shots = 8192, bonds_all = bonds_kagome_5, num_qubits = 5, initial_layout = [3, 2, 1, 0, 4]):
    circuits_vqe = [makevqeCircuit_meas_X(params, num_layers = num_layers, bonds_all = bonds_all, num_qubits = num_qubits), makevqeCircuit_meas_Y(params, num_layers = num_layers, bonds_all = bonds_all, num_qubits = num_qubits), makevqeCircuit_meas_Z(params, num_layers = num_layers, bonds_all = bonds_all, num_qubits = num_qubits)]
    expectation_ham = expectation_values(circuits_vqe, choice_backend = choice_backend, shots=shots, bonds_all = bonds_all, num_qubits = num_qubits, initial_layout = initial_layout)
    return expectation_ham


With the optimal parameters obtained via statevector minimization, we find a minimal energy of -3.79 using 2^16 shots. 

In [ ]:
ham_pqc(params_optimal, choice_backend='qasm', shots = 2**16, bonds_all = bonds_kagome_5)

Even for 2^12 = 8192 shots, the QASM energy for the optimal parameters is close to the statevector value. 

In [ ]:
ham_pqc(params_optimal, choice_backend='qasm', shots = 2**12, bonds_all = bonds_kagome_5)

In contrast, if we include realistic gate noise for the fake backend ibmq_guadalupe, we find a much higher energy. This shows that gate noise will make the classical optimization step much more difficult as the noise that the cost function experiences is largely amplified. While the shot noise can be systematically reduced by taking more shots, the gate noise induced bias remains finite. It requires the use of Quantum Error Mitigation methods to reduce this bias (see tutorial on Wed). 
See also: Z. Cai et al., arXiv:2210.00921. See also, B. McDonough et al., arXiv:2210.08611 and https://github.com/benmcdonough20/AutomatedPERTools. 

In [ ]:
ham_pqc(params_optimal, choice_backend='noisy', shots = 2**12, bonds_all = bonds_kagome_5)

Now perform the classical optimization loop that updates the HVA parameters theta_i to find the (local) minimum of expectation value of the Hamiltonian $\langle H \rangle$. We will be using a non-gradient based classical optimizer called CMA-ES, which uses an evolutionary strategy to find the global minimum of a cost function. 

In [ ]:
import cma

In [ ]:
def vqe_optimization(init_params, num_layers = 1, shots = 8192, choice_backend = 'qasm', bonds_all = bonds_kagome_5, num_qubits = 5, initial_layout = [3, 2, 1, 0, 4]):
    opts = {'maxfevals': 1000, 'tolx': 1.e-10, 'tolfun': 1.e-10, 'popsize': 100} 
    es = cma.CMAEvolutionStrategy(init_params, np.pi/2, opts)
    es.opts.set({'ftarget':1.e-15, 'maxiter':1000})
    while not es.stop():
        solutions = es.ask()
        es.tell(solutions, [ham_pqc(s, num_layers = num_layers, choice_backend=choice_backend, shots = shots, bonds_all = bonds_all, num_qubits = num_qubits, initial_layout = initial_layout) for s in solutions])
        es.disp()
        return es.result_pretty()    

The optimization is much more challenging due to the presence of shot noise, and we mostly converge to a much higher value of the energy. 

In [ ]:
init_params = np.random.uniform(-np.pi/7, np.pi/7, 6)
res = vqe_optimization(init_params, num_layers = 1, shots=2**12, choice_backend = 'qasm', bonds_all = bonds_kagome_5, num_qubits = 5, initial_layout = [3, 2, 1, 0, 4])

ToDo: 
1. Perform the optimization 10 times for different random initial values and for $2^{12}$ shots and plot a histogram of the obtained results. What is the global minimum over all ten values? How far is it from the exact GS energy?
2. What do you obtain when using $2^{14}$ shots? 

We can alleviate some of this by taking more shots. Here, we use $2^{18}$ shots, where the optimization takes a lot more time (about 2-3 min in my MacBook). 

In [ ]:
init_params = np.random.uniform(-np.pi/7, np.pi/7, 6)
res = vqe_optimization(init_params, num_layers = 1, shots=2**18, choice_backend = 'qasm', bonds_all = bonds_kagome_5, num_qubits = 5, initial_layout = [3, 2, 1, 0, 4])

Things get even more challenging if we consider the presence of gate noise. Without error mitigation, it is practically impossible to converge to a good VQE solution. Here is what we find using the realistic gate noise model from ibmq_guadalupe and using 2^8=256 shots to not wait too long. 

In [ ]:
init_params = np.random.uniform(-np.pi/7, np.pi/7, 6)
res = vqe_optimization(init_params, num_layers = 1, shots=2**8, choice_backend = 'noisy', bonds_all = bonds_kagome_5, num_qubits = 5, initial_layout = [3, 2, 1, 0, 4])

The upshot is that the HVA ansatz with one layer is insufficient to represent the ground state manifold of the five-site Kagome Heisenberg model. One way to move forward is to systematically studying deeper PQCs with more layers, which will be even more challenging to classically optimize due to increased noise and a larger parameter space. An alternative approach that circumvents the classical optimization and the quantum-classical loop is to use subspace expansion methods, see e.g. McClean et al, Phys. Rev. A 95, 042308 (2017). 

Optional Todo: 
1. Explore the noiseless QASM optimization for bigger systems with N=9 and 12 spins
2. Systematically explore the noisy optimization: 
    * vary virtual to physical qubit mapping and study the effect on the optimization performance
    * change the number of shots (be careful to not ask for too much as this is resource intensive and your kernel may crash)
    * include quantum error mitigation such as ZNE (see tutorial on Wed), e.g. using Mitiq